In [1]:
from random import choice
from pprint import pprint
import pandas as pd
import numpy as np
import seaborn as sns
import math
from kaggle_environments import evaluate, make
from kaggle_environments.envs.halite.helpers import *

In [68]:
np.set_printoptions(edgeitems=30, linewidth=100000, 
    formatter=dict(float=lambda x: "%.3g" % x))

In [293]:
list({"1-2":123}.values())[0]

123

In [155]:
observation

{'halite': [0.0,
  0.0,
  15.848,
  0.0,
  46.322,
  0.0,
  0.0,
  0.0,
  0.0,
  56.073,
  0.0,
  56.073,
  0.0,
  0.0,
  0.0,
  0.0,
  46.322,
  0.0,
  15.848,
  0.0,
  0.0,
  0.0,
  152.374,
  165.782,
  0.0,
  0.0,
  71.921,
  243.8,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  243.8,
  71.921,
  0.0,
  0.0,
  165.782,
  152.374,
  0.0,
  0.0,
  135.308,
  265.74,
  0.0,
  0.0,
  68.263,
  0.0,
  43.883,
  45.102,
  500,
  56.073,
  500,
  45.102,
  43.883,
  0.0,
  68.263,
  0.0,
  0.0,
  265.74,
  135.308,
  0.0,
  0.0,
  71.921,
  482.722,
  226.733,
  109.709,
  0.0,
  0.0,
  8.535,
  0.0,
  180.41,
  52.419,
  180.41,
  0.0,
  8.535,
  0.0,
  0.0,
  109.709,
  226.733,
  482.722,
  71.921,
  0.0,
  0.0,
  99.958,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  32.913,
  0.0,
  36.569,
  0.0,
  32.913,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  99.958,
  0.0,
  0.0,
  68.263,
  0.0,
  73.138,
  0.0,
  0.0,
  17.066,
  160.909,
  0.0,
  10.972,
  17.066,
  10.972,
  0.0,
  160

In [369]:
class myship:
    def __init__(self,ship):
        self.player_id=ship.player_id
        self.position=ship.position
        self.next_position=None
        self.state = 1
        self.id = ship.id
        self.halite = ship.halite
        self.stats = {}
        self.ddf=[]
        self.next_action=None
        self.statemap={1:"idle",2:"move_mining",3:"mining",
                       4:"move_depositing",5:"depositing",6:"create_shipyard",
                       7:"converting",8:"destroyed",101:"mining_spot"}
        self.moving_to=None
        
        
        ### Controls
        self.dist_weight=2            # weight for halite/distance calculation
        self.max_shiphalite=1000      # How much a ship should collect before returning
        self.min_cellhalite=50        # How much halite a cell should have for (continue) mining
        
    def point_from_index(self,index,size=21):
        y, x = divmod(index, size)
        return (x, (size - y - 1))
    
    def index_from_point(self,point,size=21):
        return (size - point[1] - 1) * size + point[0]
    
    def update_miningspot(self,cb):
        if self.state in [2,3]:
            cb[self.moving_to[1],self.moving_to[0]]=101
    
    def get_best_halite(self,obs,cb):
        best_halite={}
        best_halite["amount"]=0
        best_halite["pos"]=None
        
        for ix,halite in enumerate(obs.halite):          
            halite_pos=self.point_from_index(ix)
            
            if cb[halite_pos[1],halite_pos[0]] not in [3,101] and halite>=self.min_cellhalite:
                #distance to halite
                dist = math.sqrt(abs(halite_pos[1] - self.position[1]) + abs(halite_pos[0] - self.position[0]))
                dist_value=float(halite)/float(dist+0.0001*self.dist_weight)
                if dist_value>best_halite["amount"]:
                    best_halite["amount"]=dist_value
                    best_halite["pos"]=halite_pos
                    
        return best_halite["pos"]
    
    
    def getCompass(self,o_x,o_y,d_x,d_y):

        delta_x=d_x-o_x
        delta_y=d_y-o_y

        degrees = math.atan2(delta_x, delta_y)/math.pi*180

        alt=[degrees,degrees+90,degrees-90]

        for i,a in enumerate(alt):
            if a < 0:
                alt[i]=a+360

        directions=[["NORTH"],["NORTH","EAST"],["EAST"],["SOUTH","EAST"],["SOUTH"],["SOUTH","WEST"],["WEST"],["NORTH","WEST"],["NORTH"]]

        return directions[round(alt[0]/45)],directions[round(alt[1]/45)],directions[round(alt[2]/45)]   
    
    
    def update_next_action(self,cb):
        
        if self.moving_to == self.position:
            self.next_action=None
            self.next_position=self.position
        
        ddict={}
        ddict["NORTH"]=(self.position[0],self.position[1]+1)
        ddict["SOUTH"]=(self.position[0],self.position[1]-1)
        ddict["EAST"]=(self.position[0]+1,self.position[1])
        ddict["WEST"]=(self.position[0]-1,self.position[1])
        
        prio,alt1,alt2 = self.getCompass(self.position[0],self.position[1],self.moving_to[0],self.moving_to[1])
        alt=alt1+alt2
        
        for direction in prio:
            pos=ddict[direction]
            if cb[pos[1],pos[0]] in [1,2,3,4]:
                continue
            else:
                self.next_action=direction
                self.next_position=ddict[direction]
                return
            
        for direction in alt:
            pos=ddict[direction]
            if cb[pos[1],pos[0]] in [1,2,3,4]:
                continue
            else:
                self.next_action=direction
                self.next_position=ddict[direction]
                return
        
        self.next_action = None
        self.next_position=self.position
    
    
    def update(self,obs):
        self.position=self.point_from_index(obs.players[self.player_id][2][self.id][0])
        self.halite = obs.players[self.player_id][2][self.id][1]
            
    def log_stats(self,obs):
        row={}
        row["step"]=obs.step
        row["id"]=self.id
        row["position"]=self.position
        row["moving_to"]=self.moving_to
        row["state"]=self.statemap[self.state]
        row["halite"]=self.halite
        row["global_halite"]=obs.players[self.player_id][0]
        row["next_action"]=self.next_action
        row["next_position"]=self.next_position
        self.stats=row
        self.ddf.append(row)

    def update_checkboard(self,cb):
        x=self.next_position[0]
        y=self.next_position[1]
        cb[y][x]=self.state
        
    def check_destroyed(self,obs):
        return not self.id  in list(obs.players[self.player_id][2].keys())
    
    def set_action(self,obs,cb):
        if len(obs.players[self.player_id][1])==0:
            self.next_action="CONVERT"
            self.state=7
            return    
        
        # If Idle go mining
        if self.state==1:
            best_mining_spot=self.get_best_halite(obs,cb)
            self.moving_to=best_mining_spot
            cb[best_mining_spot[1],best_mining_spot[0]]=101
            self.state=2
        
        
        if self.state==2:
            if self.position==self.moving_to:
                self.next_action=None
                self.next_position=self.position
                self.state=3
                
        if self.state==3:
            if obs.halite[self.index_from_point(self.position)]<=self.min_cellhalite:
                if self.halite>=self.max_shiphalite:
                    self.moving_to=self.point_from_index(list(obs.players[self.player_id][1].values())[0])
                    self.state=4
                else: 
                    self.state=1
        
        if self.state==4:
            if self.position==self.moving_to:
                self.state=1
            
        if self.state==1:
            best_mining_spot=self.get_best_halite(obs,cb)
            self.moving_to=best_mining_spot
            cb[best_mining_spot[1],best_mining_spot[0]]=101
            self.state=2
            
        if self.state in [2,4]:
            self.update_next_action(cb)
        
        
        #self.next_action=choice(["NORTH","EAST","SOUTH","WEST",None])
        
        self.update_checkboard(cb)
        
        
        
shipids=[]
ship_list=[]

stats=[]

def agent(obs, conf):
    global stats
    checkboard=np.zeros((21,21))
    board=Board(obs,conf)
    me = board.current_player
    action={}    
    
    #check for new ships
    for ship in me.ships:
        if ship.id not in shipids:
            ship_list.append(myship(ship))
            shipids.append(ship.id)
    
    for ship in ship_list:
        #check if ship is destroyed
        if ship.check_destroyed(obs):
            ship.state=8
            ship_list.remove(ship)
            ship.log_stats(obs)
            stats.append(ship.stats)
            continue
        
        #update info
        ship.update(obs)
        
        #update cb
        ship.update_miningspot(checkboard)
        
    for ship in ship_list:
        
        #get action
        ship.set_action(obs,checkboard)
        if ship.next_action != None:
            action[ship.id]=ship.next_action
        
        #if next action is convert then remove from shiplist next round
        if ship.next_action=="CONVERT":
            ship_list.remove(ship)
        
        #logging and collect stats
        ship.log_stats(obs)
        stats.append(ship.stats)
        
    for shipyard in me.shipyards:
        if len(ship_list)<6:
            action[shipyard.id]="SPAWN"
        
    print(obs.step)
    
    return action,stats

In [370]:
env = make("halite", debug=True)
trainer = env.train([None, "random"])
observation = trainer.reset()
statistics=None
while not env.done and observation.step<500:
    my_action,statistics = agent(observation, env.configuration)
    print("My Action", my_action)
    observation = trainer.step(my_action)[0]

0
My Action {'0-1': 'CONVERT'}
1
My Action {'1-1': 'SPAWN'}
2
My Action {'2-1': 'NORTH', '1-1': 'SPAWN'}
3
My Action {'2-1': 'WEST', '3-1': 'NORTH', '1-1': 'SPAWN'}
4
My Action {'3-1': 'NORTH', '4-1': 'SOUTH', '1-1': 'SPAWN'}
5
My Action {'3-1': 'SOUTH', '4-1': 'WEST', '5-1': 'SOUTH', '1-1': 'SPAWN'}
6
My Action {'3-1': 'NORTH', '5-1': 'NORTH', '6-1': 'NORTH', '1-1': 'SPAWN'}
7
My Action {'3-1': 'SOUTH', '6-1': 'WEST', '1-1': 'SPAWN'}
8
My Action {'3-1': 'SOUTH', '6-1': 'NORTH', '8-1': 'EAST', '1-1': 'SPAWN'}
9
My Action {'6-1': 'NORTH', '8-1': 'EAST', '1-1': 'SPAWN'}
10
My Action {'6-1': 'NORTH', '8-1': 'NORTH', '10-1': 'EAST', '1-1': 'SPAWN'}
11
My Action {'6-1': 'NORTH', '8-1': 'EAST', '10-1': 'EAST', '1-1': 'SPAWN'}
12
My Action {'6-1': 'WEST', '8-1': 'EAST', '10-1': 'SOUTH', '1-1': 'SPAWN'}
13
My Action {'6-1': 'WEST', '10-1': 'EAST', '1-1': 'SPAWN'}
14
My Action {'4-1': 'SOUTH', '10-1': 'EAST', '1-1': 'SPAWN'}
15
My Action {'4-1': 'WEST', '1-1': 'SPAWN'}
16
My Action {'1-1': 'SPA

192
My Action {'8-1': 'EAST', '66-1': 'EAST', '175-1': 'NORTH'}
193
My Action {'66-1': 'EAST', '175-1': 'NORTH', '175-2': 'SOUTH'}
194
My Action {'40-1': 'EAST', '66-1': 'SOUTH', '175-2': 'SOUTH'}
195
My Action {'66-1': 'EAST', '175-2': 'NORTH', '175-3': 'EAST'}
196
My Action {'66-1': 'EAST', '175-2': 'SOUTH'}
197
My Action {'66-1': 'SOUTH', '175-2': 'NORTH'}
198
My Action {'66-1': 'EAST', '175-2': 'SOUTH'}
199
My Action {'66-1': 'EAST', '175-2': 'NORTH'}
200
My Action {'66-1': 'EAST', '175-2': 'SOUTH'}
201
My Action {'66-1': 'EAST', '175-2': 'NORTH'}
202
My Action {'8-1': 'NORTH', '66-1': 'EAST', '175-2': 'SOUTH'}
203
My Action {'8-1': 'EAST', '66-1': 'EAST', '175-1': 'SOUTH', '175-2': 'NORTH', '174-1': 'SPAWN', '174-2': 'SPAWN', '174-3': 'SPAWN'}
204
My Action {'40-1': 'EAST', '66-1': 'EAST', '175-1': 'SOUTH', '175-2': 'EAST', '204-1': 'SOUTH', '204-2': 'NORTH', '204-3': 'NORTH'}
205
My Action {'175-1': 'SOUTH', '175-2': 'WEST', '204-1': 'WEST', '204-2': 'WEST', '204-3': 'EAST'}
206


In [371]:
pd.DataFrame(statistics)

step     id  position moving_to        state  halite  global_halite  \
0        0    0-1   (5, 10)      None   converting       0           5000   
1        2    2-1   (5, 10)   (4, 11)  move_mining       0           4000   
2        3    2-1   (5, 11)   (4, 11)  move_mining       0           3500   
3        3    3-1   (5, 10)   (4, 11)  move_mining       0           3500   
4        4    2-1   (4, 11)   (4, 11)       mining       0           3000   
...    ...    ...       ...       ...          ...     ...            ...   
1214   215   66-1   (14, 8)   (14, 8)       mining     461          22898   
1215   215  175-1    (5, 6)    (5, 6)       mining     429          22898   
1216   215  175-2   (4, 11)   (4, 11)       mining    1194          22898   
1217   215  204-2   (7, 13)   (7, 16)  move_mining     461          22898   
1218   215  204-3  (10, 11)  (12, 11)  move_mining     361          22898   

     next_action next_position  
0        CONVERT          None  
1          NORTH       (5, 11)  
2           WEST       (4, 11)  
3          NORTH       (5, 11)  
4           None       (4, 11)  
...          ...           ...  
1214        None       (14, 8)  
1215        None        (5, 6)  
1216        None       (4, 11)  
1217       NORTH       (7, 14)  
1218        EAST      (11, 11)  

[1219 rows x 9 columns]

In [372]:
env.render(mode="ipython",width=800, height=600)

In [373]:
df=pd.DataFrame(statistics)
import matplotlib.pyplot as plt

fig,ax = plt.subplots(figsize=(15,7))

for cat in df["id"].unique()[:5]:
    df[df["id"]==cat].plot(x="step",y="halite",ax=ax, label=cat)
    
df.plot(x="step",y="global_halite")

<AxesSubplot:xlabel='step'>

In [358]:
df[df["id"]=="3-1"]

step   id position        state  halite nextaction
3       3  3-1  (5, 10)  move_mining       0      NORTH
5       4  3-1  (5, 11)  move_mining       0      NORTH
8       5  3-1  (5, 12)  move_mining       0      SOUTH
12      6  3-1  (5, 11)  move_mining       0      NORTH
18      7  3-1  (5, 12)  move_mining       0      SOUTH
..    ...  ...      ...          ...     ...        ...
345    62  3-1  (12, 3)       mining    1383       None
351    63  3-1  (12, 3)       mining    1501       None
357    64  3-1  (12, 3)       mining    1590       None
363    65  3-1  (12, 3)       mining    1657       None
368    66  3-1  (12, 3)    destroyed    1657       None

[64 rows x 6 columns]

In [343]:
observation

{'halite': [500,
  500,
  0.0,
  500,
  0.0,
  0.0,
  333.481,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  500,
  0.0,
  0.0,
  317.578,
  0.0,
  500,
  500,
  0.0,
  500,
  500,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  475.589,
  0.0,
  0.0,
  0.0,
  500,
  0.0,
  375,
  0.0,
  0.0,
  0.0,
  500,
  500,
  0.0,
  0.0,
  0.0,
  0.0,
  500,
  0.0,
  190.139,
  500,
  0.0,
  0.0,
  500,
  0.0,
  500,
  0.0,
  0.0,
  500,
  0.0,
  0.0,
  500,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  224.976,
  257.676,
  0.0,
  0.0,
  500,
  0.0,
  500,
  0.0,
  500,
  0.0,
  0.0,
  500,
  500,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  68,
  500,
  0.0,
  0.0,
  0.0,
  201.1,
  305.829,
  0.0,
  44.799,
  0.0,
  500,
  500,
  0.0,
  0.0,
  0.0,
  500,
  0.0,
  0.0,
  0.0,
  0.0,
  500,
  0.0,
  0.0,
  0.0,
  115.471,
  0.0,
  423.881,
  0.0,
  380.261,
  454.447,
  55.702,
  0.0,
  500,
  0.0,
  500,
  0.0,
  0.0,
  0.0,
  500,
  0.0,
  0.0,
  0.0,
  0.0,
  62.729,
  0.0,
  0.0,
  0.0,
  413